# Hafta 1: Versiyon Kontrol Sistemleri ve İşbirliği Platformları (Git & GitHub)

**Dersin Hedefleri:**
1. Versiyon kontrolünün ne olduğunu ve neden veri bilimi projelerinde kritik olduğunu anlamak.
2. Temel `git` komutlarını (`init`, `add`, `commit`, `status`, `log`, `diff`) etkin bir şekilde kullanmak.
3. Dallanma (branching) ve birleştirme (merging) kavramlarını öğrenmek ve feature-branch iş akışını uygulamak.
4. **Conflict çözme** yöntemlerini öğrenmek ve merge conflict'larını güvenle yönetmek.
5. **Git Stash** ile geçici değişiklikleri yönetmeyi öğrenmek.
6. **PyCharm IDE'si** üzerinden Git operasyonlarını görsel arayüzle gerçekleştirmek.
7. GitHub platformunu kullanarak repository oluşturmak, fork etmek, pull request açmak ve kod incelemesi yapmak.
8. Veri bilimi projelerine özgü `.gitignore` dosyası yapılandırması yapmak.
9. Takım çalışması için gerekli Git iş akışlarını ve en iyi uygulamaları kavramak.

## 1. Versiyon Kontrol Nedir ve Neden Önemlidir?

Versiyon kontrol, dosyalarınızda zaman içinde yapılan değişiklikleri takip eden, geçmişe dönmeyi ve farklı sürümleri karşılaştırmayı sağlayan bir sistemdir. Veri bilimi projelerinde versiyon kontrolün kritik önemleri:

### Veri Bilimi İçin Özel Faydalar:
- **Deney Takibi:** Farklı hiperparametreleri, özellik kombinasyonlarını ve modelleri paralel dallar halinde deneyebilirsiniz.
- **Veri Lineage:** Hangi veri ön işleme adımının hangi sonucu verdiğini takip edebilirsiniz.
- **Model Versiyonlama:** Farklı model sürümlerini karşılaştırabilir ve en iyi performansı verenine geri dönebilirsiniz.
- **Notebook Yönetimi:** Jupyter notebook'larının karmaşık durumlarını (output'lar dahil) etkili şekilde yönetebilirsiniz.
- **Takım İşbirliği:** Veri bilimciler, mühendisler ve domain uzmanları aynı proje üzerinde senkronize şekilde çalışabilir.

**Git**, günümüzde en yaygın kullanılan **dağıtık** versiyon kontrol sistemidir. Her geliştirici, projenin tam geçmişine sahip olur.

## 2. Git'in Temel Kavramları ve İş Akışı

### 2.1. Temel Kavramlar
- **Repository (Depo):** Projenizin ve geçmişinin saklandığı klasör (`.git` klasörü içerir).
- **Working Directory (Çalışma Dizini):** Dosyalarınızı düzenlediğiniz alan.
- **Staging Area (Index/Hazırlama Alanı):** Commit'e hazır olan değişikliklerin bekletildiği ara alan.
- **Commit:** Projenizin belirli bir andaki anlık görüntüsü. SHA hash ile benzersiz kimliği vardır.
- **Branch (Dal):** Projenin paralel bir geliştirme hattı. Bağımsız özellik geliştirme için kullanılır.
- **HEAD:** Şu anda çalıştığınız commit'i gösteren pointer.
- **Origin:** Varsayılan uzak repository (remote) adı.

### 2.2. Git İş Akışı (Git Workflow)
```
Working Directory -> Staging Area -> Local Repository -> Remote Repository
     (git add)        (git commit)      (git push)
```

## 3. Pratik Uygulama: Kapsamlı Git Projesi

Bu bölümde, gerçek bir veri bilimi projesi simüle ederek Git'in tüm özelliklerini deneyimleyeceğiz.

In [ ]:
import os
import subprocess
import pandas as pd
import numpy as np
import shutil
import time

# Örnek proje için çalışma dizini oluşturalım
project_name = "makine_ogrenmesi_projesi"
if os.path.exists(project_name):
    shutil.rmtree(project_name)

os.makedirs(project_name)
original_dir = os.getcwd()
os.chdir(project_name)

print(f"Çalışma dizini: {os.getcwd()}")

### 3.1. Gelişmiş Git Komut Fonksiyonu

In [ ]:
def run_git_command(command, description="", show_output=True, check_error=True):
    """Geliştirilmiş Git komut çalıştırıcı."""
    if show_output:
        print(f"\n--- {description} ---")
        print(f"Komut: git {command}")

    result = subprocess.run(
        ["git"] + command.split(),
        capture_output=True,
        text=True,
        cwd=os.getcwd()
    )

    if show_output:
        if result.stdout:
            print("Çıktı:", result.stdout.strip())
        if result.stderr and check_error:
            print("Hata/Uyarı:", result.stderr.strip())

    return result.returncode == 0, result.stdout, result.stderr

def git_status():
    """Kısa git status komutu."""
    success, stdout, stderr = run_git_command("status --porcelain", "", False)
    return stdout.strip().split('\n') if stdout.strip() else []

# Repository başlatma ve temel yapılandırma
run_git_command("init", "Git repository'si başlatılıyor")
run_git_command("config user.name 'Veri Bilimci'", "Kullanıcı adı ayarlanıyor")
run_git_command("config user.email 'veri@example.com'", "E-posta ayarlanıyor")

### 3.2. Proje Yapısını Oluşturma

In [ ]:
# Kapsamlı proje yapısı oluşturma
def create_project_structure():
    """Gerçekçi bir ML projesi yapısı oluşturur."""

    # Klasör yapısı
    folders = [
        "data/raw",
        "data/processed",
        "data/external",
        "notebooks/exploratory",
        "notebooks/modeling",
        "src/data",
        "src/features",
        "src/models",
        "src/visualization",
        "tests",
        "models",
        "reports/figures",
        "configs"
    ]

    for folder in folders:
        os.makedirs(folder, exist_ok=True)
        # Python paketleri için __init__.py
        if 'src/' in folder:
            open(os.path.join(folder, "__init__.py"), 'w').close()

# README.md - Kapsamlı proje dokümantasyonu
readme_content = """# Makine Öğrenmesi Projesi

Bu proje, müşteri churn tahmini için end-to-end bir makine öğrenmesi pipeline'ı içerir.

## Proje Yapısı

```
├── data/
│   ├── raw/                 # Ham veri dosyaları
│   ├── processed/           # İşlenmiş veri
│   └── external/            # Harici veri kaynakları
├── notebooks/
│   ├── exploratory/         # Keşifsel veri analizi
│   └── modeling/            # Model geliştirme
├── src/
│   ├── data/                # Veri işleme modülleri
│   ├── features/            # Özellik mühendisliği
│   ├── models/              # Model eğitimi ve değerlendirme
│   └── visualization/       # Görselleştirme araçları
├── tests/                   # Unit testler
├── models/                  # Eğitilmiş model dosyaları
├── reports/                 # Analiz raporları
└── configs/                 # Yapılandırma dosyaları
```

## Kurulum

```bash
pip install -r requirements.txt
```

## Kullanım

1. Veri hazırlama: `python src/data/make_dataset.py`
2. Özellik mühendisliği: `python src/features/build_features.py`
3. Model eğitimi: `python src/models/train_model.py`

## Katkıda Bulunma

1. Fork edin
2. Feature branch oluşturun (`git checkout -b feature/yeni-ozellik`)
3. Değişikliklerinizi commit edin
4. Branch'ınızı push edin
5. Pull Request açın

## Lisans

MIT License
"""

# Temel dosyaları oluştur
create_project_structure()

with open("README.md", "w", encoding="utf-8") as f:
    f.write(readme_content)

# requirements.txt
requirements = """pandas>=1.3.0
numpy>=1.21.0
scikit-learn>=1.0.0
matplotlib>=3.5.0
seaborn>=0.11.0
jupyter>=1.0.0
pytest>=6.0.0
"""

with open("requirements.txt", "w") as f:
    f.write(requirements)

print("Proje yapısı oluşturuldu.")

### 3.3. Kaynak Kod Modülleri Oluşturma

In [ ]:
# src/data/make_dataset.py - Veri yükleme modülü
data_module = """
import pandas as pd
import numpy as np
from pathlib import Path

def load_raw_data(file_path):
    \"\"\"Ham veriyi yükler ve temel temizlik yapar.\"\"\"
    try:
        df = pd.read_csv(file_path)
        print(f"Veri yüklendi: {df.shape[0]} satır, {df.shape[1]} sütun")
        return df
    except FileNotFoundError:
        print(f"Hata: {file_path} dosyası bulunamadı")
        return None

def basic_data_validation(df):
    \"\"\"Temel veri doğrulama kontrolleri.\"\"\"
    validation_results = {
        'null_counts': df.isnull().sum(),
        'data_types': df.dtypes,
        'duplicate_rows': df.duplicated().sum()
    }
    return validation_results

def save_processed_data(df, output_path):
    \"\"\"İşlenmiş veriyi kaydeder.\"\"\"
    df.to_csv(output_path, index=False)
    print(f"İşlenmiş veri kaydedildi: {output_path}")

if __name__ == "__main__":
    # Örnek kullanım
    print("Veri yükleme modülü çalıştırılıyor...")
"""

with open("src/data/make_dataset.py", "w", encoding="utf-8") as f:
    f.write(data_module)

# src/features/build_features.py - Özellik mühendisliği
features_module = """
import pandas as pd
import numpy as np
from sklearn.preprocessing import StandardScaler, LabelEncoder

def create_age_groups(df, age_column='age'):
    \"\"\"Yaş grupları oluşturur.\"\"\"
    df = df.copy()
    df['age_group'] = pd.cut(df[age_column],
                            bins=[0, 25, 35, 50, 100],
                            labels=['young', 'adult', 'middle', 'senior'])
    return df

def encode_categorical_features(df, categorical_columns):
    \"\"\"Kategorik özellikleri kodlar.\"\"\"
    df = df.copy()
    encoders = {}

    for col in categorical_columns:
        if col in df.columns:
            le = LabelEncoder()
            df[col] = le.fit_transform(df[col].astype(str))
            encoders[col] = le

    return df, encoders

def scale_numerical_features(df, numerical_columns):
    \"\"\"Sayısal özellikleri ölçeklendirir.\"\"\"
    df = df.copy()
    scaler = StandardScaler()

    df[numerical_columns] = scaler.fit_transform(df[numerical_columns])

    return df, scaler

if __name__ == "__main__":
    print("Özellik mühendisliği modülü çalıştırılıyor...")
"""

with open("src/features/build_features.py", "w", encoding="utf-8") as f:
    f.write(features_module)

# Örnek veri dosyası
np.random.seed(42)
sample_data = pd.DataFrame({
    'customer_id': range(1, 1001),
    'age': np.random.randint(18, 80, 1000),
    'income': np.random.normal(50000, 15000, 1000),
    'tenure': np.random.randint(1, 120, 1000),
    'city': np.random.choice(['Istanbul', 'Ankara', 'Izmir', 'Bursa'], 1000),
    'churn': np.random.choice([0, 1], 1000, p=[0.7, 0.3])
})

sample_data.to_csv("data/raw/customer_data.csv", index=False)
print("Örnek veri dosyası oluşturuldu.")

### 3.4. İlk Commit ve Geçmiş Takibi

In [ ]:
# .gitignore dosyası - Veri bilimi projeleri için kapsamlı
gitignore_content = """# Veri bilimi projesi için .gitignore

# Büyük veri dosyaları
*.csv
!data/raw/customer_data.csv  # Örnek veri dosyası hariç
*.parquet
*.hdf5
*.xlsx
*.h5
*.db
*.sqlite

# Model dosyaları
*.pkl
*.joblib
*.model
*.h5
*.pb
models/*.pkl
models/*.joblib

# Jupyter Notebook
.ipynb_checkpoints/
*/.ipynb_checkpoints/*
*.ipynb_checkpoints

# Python
__pycache__/
*.py[cod]
*$py.class
*.so
.Python
build/
develop-eggs/
dist/
downloads/
eggs/
.eggs/
lib/
lib64/
parts/
sdist/
var/
wheels/
*.egg-info/
.installed.cfg
*.egg

# Virtual environments
venv/
env/
ENV/
.venv/
.conda/

# IDE files
.vscode/
.idea/
*.swp
*.swo
*~

# OS files
.DS_Store
.DS_Store?
._*
.Spotlight-V100
.Trashes
ehthumbs.db
Thumbs.db

# Environment variables
.env
.env.local
.env.production

# Logs
*.log
logs/

# Cache
.cache/
.pytest_cache/

# Temporary files
*.tmp
*.temp
tmp/

# MLflow
mlruns/
mlartifacts/

# DVC
.dvc/
*.dvc

# Airflow
airflow.db
airflow-webserver.pid
"""

with open(".gitignore", "w", encoding="utf-8") as f:
    f.write(gitignore_content)

# İlk commit
run_git_command("add .", "Tüm dosyalar staging area'ya ekleniyor")
run_git_command('commit -m "İlk commit: Proje yapısı ve temel modüller eklendi\n\n- Kapsamlı klasör yapısı oluşturuldu\n- Veri işleme ve özellik mühendisliği modülleri eklendi\n- .gitignore dosyası yapılandırıldı\n- Örnek veri dosyası eklendi"',
                "İlk commit yapılıyor")

run_git_command("log --oneline", "Commit geçmişi")

## 4. Branching Stratejileri ve Gelişmiş İş Akışları

### 4.1. Feature Branch İş Akışı

Profesyonel projelerde her yeni özellik için ayrı dal oluşturmak standart uygulamadır.

In [ ]:
# Mevcut dalları ve durumu görme
run_git_command("branch -v", "Mevcut dallar ve son commit'ler")
run_git_command("status", "Çalışma dizini durumu")

# Feature branch oluşturma - Model geliştirme
run_git_command("checkout -b feature/model-development",
                "Model geliştirme dalı oluşturuluyor")

# Model eğitimi modülü
model_module = """
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score, classification_report, confusion_matrix
import joblib
from datetime import datetime

class ChurnPredictor:
    \"\"\"Müşteri churn tahmini için model sınıfı.\"\"\"

    def __init__(self, model_type='random_forest'):
        self.model_type = model_type
        self.model = None
        self.is_trained = False

    def get_model(self):
        \"\"\"Model tipine göre model döndürür.\"\"\"
        if self.model_type == 'random_forest':
            return RandomForestClassifier(n_estimators=100, random_state=42)
        elif self.model_type == 'logistic':
            return LogisticRegression(random_state=42)
        else:
            raise ValueError(f"Desteklenmeyen model tipi: {self.model_type}")

    def train(self, X_train, y_train):
        \"\"\"Modeli eğitir.\"\"\"
        self.model = self.get_model()
        self.model.fit(X_train, y_train)
        self.is_trained = True
        print(f"{self.model_type} modeli eğitildi.")

    def predict(self, X_test):
        \"\"\"Tahmin yapar.\"\"\"
        if not self.is_trained:
            raise ValueError("Model henüz eğitilmemiş!")
        return self.model.predict(X_test)

    def evaluate(self, X_test, y_test):
        \"\"\"Model performansını değerlendirir.\"\"\"
        predictions = self.predict(X_test)
        accuracy = accuracy_score(y_test, predictions)
        report = classification_report(y_test, predictions)

        return {
            'accuracy': accuracy,
            'classification_report': report,
            'predictions': predictions
        }

    def save_model(self, filepath):
        \"\"\"Modeli kaydeder.\"\"\"
        if not self.is_trained:
            raise ValueError("Eğitilmemiş model kaydedilemez!")

        model_data = {
            'model': self.model,
            'model_type': self.model_type,
            'training_date': datetime.now().isoformat()
        }

        joblib.dump(model_data, filepath)
        print(f"Model kaydedildi: {filepath}")

if __name__ == "__main__":
    print("Churn tahmin modeli modülü hazır.")
"""

with open("src/models/train_model.py", "w", encoding="utf-8") as f:
    f.write(model_module)

# Model geliştirme dalındaki değişiklikleri commit etme
run_git_command("add .", "Model modülü ekleniyor")
run_git_command('commit -m "Model eğitimi modülü eklendi\n\n- ChurnPredictor sınıfı oluşturuldu\n- Random Forest ve Logistic Regression desteği\n- Model değerlendirme ve kaydetme fonksiyonları"',
                "Model modülü commit'i")

## 5. Git Stash: Geçici Değişiklikleri Yönetme

Git Stash, henüz commit etmeye hazır olmayan değişiklikleri geçici olarak saklamanıza olanak tanır.

In [ ]:
# Stash senaryosu: Yarım kalmış bir özellik üzerinde çalışıyoruz
print("\n=== GIT STASH SENARYOSU ===")

# Visualization modülü üzerinde çalışmaya başlıyoruz
viz_module_incomplete = """
import matplotlib.pyplot as plt
import seaborn as sns
import pandas as pd

def plot_age_distribution(df):
    \"\"\"Yaş dağılımını çizer.\"\"\"
    plt.figure(figsize=(10, 6))
    plt.hist(df['age'], bins=30, alpha=0.7)
    plt.title('Müşteri Yaş Dağılımı')
    plt.xlabel('Yaş')
    plt.ylabel('Frekans')
    # TODO: Daha fazla stil ayarı eklenecek
    # TODO: Outlier analizi eklenecek
"""

with open("src/visualization/plots.py", "w", encoding="utf-8") as f:
    f.write(viz_module_incomplete)

run_git_command("add src/visualization/plots.py", "Yarım kalmış dosya ekleniyor")
run_git_command("status", "Yarım kalmış çalışma durumu")

# Acil bir düzeltme için ana dala geçmemiz gerekiyor
# Ama yarım kalmış işimizi kaybetmek istemiyoruz
print("\n--- Acil düzeltme gerekli! Yarım kalmış işi stash'liyoruz ---")

run_git_command("stash push -m 'Görselleştirme modülü yarım kalmış - TODO listesi var'",
                "Değişiklikler stash'leniyor")

run_git_command("status", "Stash sonrası temiz çalışma dizini")
run_git_command("stash list", "Stash listesi")

# Ana dala geçiş yapabiliriz
run_git_command("checkout main", "Ana dala geçiş")

# Acil düzeltme: README'de bir typo
with open("README.md", "r", encoding="utf-8") as f:
    content = f.read()

# Basit bir düzeltme
content = content.replace("Katkıda Bulunma", "Katkıda Bulunma")  # Aslında değişiklik yok, demo için
content = content.replace("MIT License", "MIT License\n\n## Versiyon\n\nv1.0.0")

with open("README.md", "w", encoding="utf-8") as f:
    f.write(content)

run_git_command("add README.md", "README düzeltmesi")
run_git_command('commit -m "Hotfix: README.md güncellemesi - versiyon bilgisi eklendi"',
                "Acil düzeltme commit'i")

# Şimdi feature branch'e geri dönüp stash'lenmiş işimizi geri alabiliriz
run_git_command("checkout feature/model-development", "Feature dalına geri dönüş")

# Stash'lenmiş değişiklikleri geri alma
run_git_command("stash pop", "Stash'lenmiş değişiklikler geri alınıyor")
run_git_command("status", "Stash pop sonrası durum")

# Şimdi görselleştirme modülünü tamamlayabiliriz
viz_module_complete = """
import matplotlib.pyplot as plt
import seaborn as sns
import pandas as pd
import numpy as np

def plot_age_distribution(df, save_path=None):
    \"\"\"Yaş dağılımını çizer.\"\"\"
    plt.figure(figsize=(12, 8))

    # Histogram
    plt.subplot(2, 2, 1)
    plt.hist(df['age'], bins=30, alpha=0.7, color='skyblue', edgecolor='black')
    plt.title('Müşteri Yaş Dağılımı')
    plt.xlabel('Yaş')
    plt.ylabel('Frekans')
    plt.grid(True, alpha=0.3)

    # Box plot
    plt.subplot(2, 2, 2)
    plt.boxplot(df['age'])
    plt.title('Yaş Dağılımı - Box Plot')
    plt.ylabel('Yaş')

    # Churn'e göre yaş dağılımı
    plt.subplot(2, 2, 3)
    if 'churn' in df.columns:
        for churn_val in df['churn'].unique():
            subset = df[df['churn'] == churn_val]['age']
            plt.hist(subset, alpha=0.7, label=f'Churn: {churn_val}', bins=20)
        plt.legend()
        plt.title('Churn Durumuna Göre Yaş Dağılımı')
        plt.xlabel('Yaş')
        plt.ylabel('Frekans')

    # İstatistikler
    plt.subplot(2, 2, 4)
    stats_text = f"""İstatistikler:
    Ortalama: {df['age'].mean():.1f}
    Medyan: {df['age'].median():.1f}
    Std. Sapma: {df['age'].std():.1f}
    Min: {df['age'].min()}
    Max: {df['age'].max()}"""
    plt.text(0.1, 0.5, stats_text, fontsize=12, verticalalignment='center')
    plt.axis('off')

    plt.tight_layout()

    if save_path:
        plt.savefig(save_path, dpi=300, bbox_inches='tight')
        print(f"Grafik kaydedildi: {save_path}")

    plt.show()

def plot_correlation_matrix(df, save_path=None):
    \"\"\"Korelasyon matrisini çizer.\"\"\"
    numerical_cols = df.select_dtypes(include=[np.number]).columns
    correlation_matrix = df[numerical_cols].corr()

    plt.figure(figsize=(10, 8))
    sns.heatmap(correlation_matrix, annot=True, cmap='coolwarm', center=0,
                square=True, linewidths=0.5)
    plt.title('Özellikler Arası Korelasyon Matrisi')
    plt.tight_layout()

    if save_path:
        plt.savefig(save_path, dpi=300, bbox_inches='tight')
        print(f"Korelasyon matrisi kaydedildi: {save_path}")

    plt.show()

def plot_churn_analysis(df, save_path=None):
    \"\"\"Churn analizini görselleştirir.\"\"\"
    if 'churn' not in df.columns:
        print("Churn sütunu bulunamadı!")
        return

    fig, axes = plt.subplots(2, 2, figsize=(15, 12))

    # Churn oranı
    churn_counts = df['churn'].value_counts()
    axes[0, 0].pie(churn_counts.values, labels=['Kalan', 'Ayrılan'],
                   autopct='%1.1f%%', startangle=90)
    axes[0, 0].set_title('Churn Oranı')

    # Yaşa göre churn
    axes[0, 1].boxplot([df[df['churn']==0]['age'], df[df['churn']==1]['age']])
    axes[0, 1].set_xticklabels(['Kalan', 'Ayrılan'])
    axes[0, 1].set_title('Yaşa Göre Churn')
    axes[0, 1].set_ylabel('Yaş')

    # Gelire göre churn
    if 'income' in df.columns:
        axes[1, 0].boxplot([df[df['churn']==0]['income'], df[df['churn']==1]['income']])
        axes[1, 0].set_xticklabels(['Kalan', 'Ayrılan'])
        axes[1, 0].set_title('Gelire Göre Churn')
        axes[1, 0].set_ylabel('Gelir')

    # Şehire göre churn
    if 'city' in df.columns:
        city_churn = df.groupby('city')['churn'].mean()
        axes[1, 1].bar(city_churn.index, city_churn.values)
        axes[1, 1].set_title('Şehre Göre Churn Oranı')
        axes[1, 1].set_ylabel('Churn Oranı')
        axes[1, 1].tick_params(axis='x', rotation=45)

    plt.tight_layout()

    if save_path:
        plt.savefig(save_path, dpi=300, bbox_inches='tight')
        print(f"Churn analizi kaydedildi: {save_path}")

    plt.show()

if __name__ == "__main__":
    print("Görselleştirme modülü hazır.")

    # Test
    try:
        test_df = pd.read_csv("data/raw/customer_data.csv")
        plot_age_distribution(test_df)
    except FileNotFoundError:
        print("Test verisi bulunamadı.")
"""

with open("src/visualization/plots.py", "w", encoding="utf-8") as f:
    f.write(viz_module_complete)

run_git_command("add .", "Görselleştirme modülü tamamlandı")
run_git_command('commit -m "Görselleştirme modülü tamamlandı\n\n- Yaş dağılımı ve churn analiz grafikleri\n- Korelasyon matrisi görselleştirmesi\n- Grafik kaydetme fonksiyonalitesi\n- Test kodu eklendi"',
                "Görselleştirme modülü commit'i")

## 6. Merge Conflicts: Çakışma Çözme

Gerçek projelerde en sık karşılaşılan durumlardan biri merge conflict'lardır.
Bu durumu simüle edelim ve çözme yöntemlerini öğrenelim.

In [ ]:
print("\n=== MERGE CONFLICT SENARYOSU ===")

# Ana dalda da görselleştirme üzerinde çalışan başka bir geliştirici olduğunu simüle edelim
run_git_command("checkout main", "Ana dala geçiş")

# Ana dalda basit bir görselleştirme modülü oluşturalım (conflict için)
simple_viz_module = """
import matplotlib.pyplot as plt

def simple_plot(df):
    \"\"\"Basit bir grafik çizer.\"\"\"
    plt.figure(figsize=(8, 6))
    plt.hist(df['age'], bins=20)
    plt.title('Yaş Dağılımı - Basit Versiyon')
    plt.show()

def basic_statistics(df):
    \"\"\"Temel istatistikleri gösterir.\"\"\"
    print(f"Ortalama yaş: {df['age'].mean():.2f}")
    print(f"Minimum yaş: {df['age'].min()}")
    print(f"Maksimum yaş: {df['age'].max()}")

if __name__ == "__main__":
    print("Basit görselleştirme modülü")
"""

# Aynı dosyayı ana dalda da oluşturalım
with open("src/visualization/plots.py", "w", encoding="utf-8") as f:
    f.write(simple_viz_module)

run_git_command("add .", "Ana dalda basit görselleştirme ekleniyor")
run_git_command('commit -m "Ana dalda basit görselleştirme modülü eklendi"',
                "Ana dalda görselleştirme commit'i")

# Şimdi feature branch'i merge etmeye çalışalım - conflict çıkacak!
print("\n--- Merge conflict oluşturmaya çalışıyoruz ---")
success, stdout, stderr = run_git_command("merge feature/model-development",
                                         "Feature dalını merge etmeye çalışıyor",
                                         check_error=False)

if not success:
    print("Beklenen conflict oluştu!")
    run_git_command("status", "Conflict durumu")

    # Conflict olan dosyayı inceleyelim
    print("\n--- Conflict olan dosya içeriği ---")
    try:
        with open("src/visualization/plots.py", "r", encoding="utf-8") as f:
            conflict_content = f.read()
        print(conflict_content[:500] + "..." if len(conflict_content) > 500 else conflict_content)
    except:
        print("Conflict dosyası okunamadı")

### 6.1. Conflict Çözme Stratejileri

Git conflict marker'ları:
- `<<<<<<< HEAD`: Mevcut dalın değişiklikleri başlangıcı
- `=======`: Değişikliklerin ayrımı
- `>>>>>>> branch-name`: Merge edilen dalın değişiklikleri sonu

**Çözme Yöntemleri:**
1. **Manuel çözme**: Dosyayı editörde açıp marker'ları temizleme
2. **Tool kullanma**: `git mergetool` komutu
3. **Bir tarafı seçme**: `git checkout --theirs/--ours filename`

In [ ]:
# Conflict'i çözelim - feature branch'deki gelişmiş versiyonu alalım
print("\n--- Conflict çözülüyor ---")

# Feature branch'deki versiyonu seçiyoruz (daha kapsamlı olduğu için)
run_git_command("checkout --theirs src/visualization/plots.py",
                "Feature branch'deki versiyon seçiliyor")

# Conflict çözüldükten sonra commit etmeliyiz
run_git_command("add src/visualization/plots.py", "Çözülmüş dosya ekleniyor")
run_git_command('commit -m "Merge conflict çözüldü: Gelişmiş görselleştirme modülü korundu"',
                "Conflict çözüm commit'i")

run_git_command("log --oneline --graph", "Merge sonrası commit geçmişi")

## 7. PyCharm ile Git Operasyonları

PyCharm IDE'si, Git operasyonları için güçlü görsel araçlar sunar.
Bu bölümde PyCharm'daki temel Git işlemlerini öğreneceğiz.

### 7.1. PyCharm Git Menüsü ve Kısayollar

**Ana Git İşlemleri:**

1. **VCS Menüsü:**
   - `VCS → Git → Clone...` - Repository klonlama
   - `VCS → Git → Branches...` - Dal yönetimi (Ctrl+Shift+`)
   - `VCS → Git → Merge...` - Dal birleştirme
   - `VCS → Git → Stash Changes...` - Değişiklikleri saklama

2. **Commit İşlemleri:**
   - `Ctrl+K` - Commit penceresi
   - `Ctrl+Shift+K` - Push to remote
   - `Ctrl+T` - Update project (pull)

3. **Dosya Düzeyinde İşlemler:**
   - `Ctrl+Alt+Z` - Rollback (dosyayı geri al)
   - `Ctrl+D` - Compare with branch/tag
   - `Alt+Shift+C` - View recent changes

**PyCharm Git Özellikleri:**

| Özellik | Açıklama | Kısayol |
|---------|----------|---------|
| **Git Log** | Commit geçmişini görsel olarak gösterir | Alt+9 |
| **Changes View** | Değişen dosyaları listeler | Alt+9 |
| **Diff Viewer** | Dosya değişikliklerini yan yana gösterir | Ctrl+D |
| **Blame/Annotate** | Her satırın kim tarafından yazıldığını gösterir | Sağ tık → Git → Annotate |
| **Shelf** | Git stash'e alternatif, PyCharm'a özel | VCS → Shelf |

### 7.2. PyCharm'da Branch Management

**PyCharm Branch İşlemleri:**

1. **Yeni Branch Oluşturma:**
   - Sağ alt köşedeki branch adına tıklayın
   - "+ New Branch" seçin
   - Branch adını girin

2. **Branch Değiştirme:**
   - Branch popup'ında (Ctrl+Shift+`) istenen branch'e çift tıklayın
   - Veya "Checkout" butonunu kullanın

3. **Branch Silme:**
   - Branch listesinde branch'e sağ tıklayın
   - "Delete" seçin

4. **Branch Karşılaştırma:**
   - İki branch'i seçin
   - "Compare" tıklayın
   - Dosya farklarını görüntüleyin

### 7.3. PyCharm Commit İş Akışı

**Commit Penceresi Özellikleri:**

1. **Changed Files Panel:**
   - Değişen dosyalar listesi
   - Her dosya için diff gösterimi
   - Seçici commit (bazı dosyaları commit'e dahil etmeme)

2. **Commit Message:**
   - Commit mesajı editörü
   - Spell check
   - Commit message templates

3. **Before Commit Checks:**
   - Code analysis (code inspection)
   - Reformat code
   - Optimize imports
   - Perform code analysis

4. **Commit Options:**
   - Amend commit (son commit'i değiştir)
   - Sign-off commit
   - Custom commit commands

### 7.4. PyCharm Merge ve Conflict Resolution

**PyCharm Merge Tool Özellikleri:**

1. **Three-way Merge View:**
   - Sol panel: Your changes (local)
   - Orta panel: Result (merge sonucu)
   - Sağ panel: Their changes (remote)

2. **Conflict Resolution Actions:**
   - Accept yours (yeşil ok) - Kendi değişikliğinizi kabul edin
   - Accept theirs (mavi ok) - Diğer tarafın değişikliğini kabul edin
   - Accept both - Her iki değişikliği de kabul edin
   - Manual edit - Manuel olarak düzenleyin

3. **Navigation:**
   - F7: Next conflict
   - Shift+F7: Previous conflict
   - Ctrl+Shift+Z: Revert conflict resolution

**PyCharm'da Merge Conflict Çözme Adımları:**
1. Conflict oluştuğunda PyCharm otomatik olarak merge tool'u açar
2. Her conflict için uygun action'ı seçin
3. "Apply" butonuna tıklayın
4. Tüm conflict'lar çözüldükten sonra merge commit'ini yapın

## 8. GitHub İş Akışları ve Best Practices

### 8.1. Repository Yönetimi

In [ ]:
# GitHub için örnek workflow dosyası oluşturalım
github_dir = ".github/workflows"
os.makedirs(github_dir, exist_ok=True)

ci_workflow = """name: CI/CD Pipeline

on:
  push:
    branches: [ main, develop ]
  pull_request:
    branches: [ main ]

jobs:
  test:
    runs-on: ubuntu-latest
    strategy:
      matrix:
        python-version: [3.8, 3.9, '3.10']

    steps:
    - uses: actions/checkout@v3

    - name: Set up Python ${{ matrix.python-version }}
      uses: actions/setup-python@v3
      with:
        python-version: ${{ matrix.python-version }}

    - name: Install dependencies
      run: |
        python -m pip install --upgrade pip
        pip install -r requirements.txt
        pip install pytest pytest-cov

    - name: Run tests
      run: |
        pytest tests/ --cov=src --cov-report=xml

    - name: Upload coverage to Codecov
      uses: codecov/codecov-action@v3
      with:
        file: ./coverage.xml

  lint:
    runs-on: ubuntu-latest

    steps:
    - uses: actions/checkout@v3

    - name: Set up Python
      uses: actions/setup-python@v3
      with:
        python-version: '3.9'

    - name: Install linting tools
      run: |
        python -m pip install --upgrade pip
        pip install flake8 black isort

    - name: Run flake8
      run: flake8 src/ tests/

    - name: Check code formatting with black
      run: black --check src/ tests/

    - name: Check import sorting with isort
      run: isort --check-only src/ tests/
"""

with open(f"{github_dir}/ci.yml", "w", encoding="utf-8") as f:
    f.write(ci_workflow)

# Pull request template
pr_template_dir = ".github"
pr_template = """## Açıklama
Bu PR'ın amacını ve yaptığı değişiklikleri kısaca açıklayın.

## Değişiklik Türü
- [ ] Bug fix (kırılgan olmayan değişiklik - mevcut sorunu çözer)
- [ ] New feature (kırılgan olmayan değişiklik - yeni fonksiyonalite ekler)
- [ ] Breaking change (mevcut fonksiyonaliteyi etkileyen değişiklik)
- [ ] Documentation update (dokümantasyon güncellemesi)

## Test Edilme Durumu
- [ ] Unit testler yazıldı/güncellendi
- [ ] Tüm testler geçiyor
- [ ] Manuel test yapıldı

## Checklist
- [ ] Kodun stil kurallarına uygunluğu kontrol edildi
- [ ] Self-review yapıldı
- [ ] Kod açıklamalı (gerektiği yerlerde)
- [ ] İlgili dokümantasyon güncellendi
- [ ] Değişiklikler test edildi
- [ ] Dependent değişiklikler merge edildi

## Screenshots (gerekirse)
İlgili ekran görüntüleri ekleyin.

## Additional Notes
Ek notlar, bağımlılıklar, bilinen sorunlar vb.
"""

with open(f"{pr_template_dir}/pull_request_template.md", "w", encoding="utf-8") as f:
    f.write(pr_template)

# Issue template
issue_template_dir = ".github/ISSUE_TEMPLATE"
os.makedirs(issue_template_dir, exist_ok=True)

bug_template = """---
name: Bug Report
about: Bir bug bildirmek için bu template'i kullanın
title: '[BUG] '
labels: bug
assignees: ''
---

## Bug Açıklaması
Karşılaştığınız bug'ı açık ve kısa bir şekilde tanımlayın.

## Tekrar Etme Adımları
Bug'ı tekrar etmek için gereken adımlar:
1. '...' sayfasına git
2. '...' butonuna tıkla
3. '...' alanında aşağı kaydır
4. Hata görüntülenir

## Beklenen Davranış
Ne olmasını bekliyordunuz?

## Ekran Görüntüleri
Uygunsa, sorunu açıklamaya yardımcı olacak ekran görüntüleri ekleyin.

## Ortam Bilgileri
- OS: [örn. iOS]
- Python Version: [örn. 3.9]
- Browser [örn. chrome, safari]
- Version [örn. 22]

## Ek Bağlam
Bug hakkında başka herhangi bir bilgi.
"""

with open(f"{issue_template_dir}/bug_report.md", "w", encoding="utf-8") as f:
    f.write(bug_template)

# Test dosyası oluşturalım
test_content = """
import pytest
import pandas as pd
import sys
import os

# src klasörünü path'e ekle
sys.path.insert(0, os.path.join(os.path.dirname(__file__), '..', 'src'))

from data.make_dataset import load_raw_data, basic_data_validation
from features.build_features import create_age_groups, encode_categorical_features

class TestDataModule:
    \"\"\"Veri modülü testleri.\"\"\"

    def test_basic_data_validation(self):
        \"\"\"Veri doğrulama fonksiyonunu test eder.\"\"\"
        # Test verisi oluştur
        test_df = pd.DataFrame({
            'age': [25, 30, None, 45],
            'income': [50000, 60000, 70000, 80000],
            'city': ['Istanbul', 'Ankara', 'Istanbul', 'Izmir']
        })

        result = basic_data_validation(test_df)

        # Null sayısını kontrol et
        assert result['null_counts']['age'] == 1
        assert result['null_counts']['income'] == 0

        # Veri tiplerini kontrol et
        assert 'age' in result['data_types']
        assert 'income' in result['data_types']

class TestFeatureModule:
    \"\"\"Özellik mühendisliği modülü testleri.\"\"\"

    def test_create_age_groups(self):
        \"\"\"Yaş grupları oluşturma fonksiyonunu test eder.\"\"\"
        test_df = pd.DataFrame({
            'age': [20, 30, 40, 60],
            'income': [40000, 50000, 60000, 70000]
        })

        result_df = create_age_groups(test_df)

        # Yeni sütunun eklendiğini kontrol et
        assert 'age_group' in result_df.columns

        # Kategorilerin doğruluğunu kontrol et
        expected_groups = ['young', 'adult', 'middle', 'senior']
        for group in result_df['age_group'].dropna():
            assert group in expected_groups

    def test_encode_categorical_features(self):
        \"\"\"Kategorik özellik kodlama fonksiyonunu test eder.\"\"\"
        test_df = pd.DataFrame({
            'city': ['Istanbul', 'Ankara', 'Istanbul', 'Izmir'],
            'age': [25, 30, 35, 40]
        })

        result_df, encoders = encode_categorical_features(test_df, ['city'])

        # Kodlama yapıldığını kontrol et
        assert result_df['city'].dtype in ['int64', 'int32']

        # Encoder'ın döndürüldüğünü kontrol et
        assert 'city' in encoders
        assert hasattr(encoders['city'], 'classes_')

if __name__ == "__main__":
    pytest.main([__file__])
"""

with open("tests/test_modules.py", "w", encoding="utf-8") as f:
    f.write(test_content)

print("GitHub workflow dosyaları ve testler oluşturuldu.")

### 8.2. GitHub Flow vs Git Flow

**GitHub Flow (Basit):**
1. `main` branch her zaman deployable
2. Yeni özellik için branch oluştur
3. Değişiklikleri commit et ve push et
4. Pull Request aç
5. Code review yap
6. Merge et ve branch'i sil

**Git Flow (Karmaşık):**
- `main`: Production-ready kod
- `develop`: Geliştirme branch'i
- `feature/*`: Özellik branch'leri
- `release/*`: Release hazırlığı
- `hotfix/*`: Acil düzeltmeler

## 9. İleri Düzey Git Teknikleri

### 9.1. Git Hooks ve Automation

In [ ]:
# Pre-commit hook oluşturalım (kendi hook sistemimizi simüle edelim)
hooks_dir = ".git/hooks"
if os.path.exists(hooks_dir):
    pre_commit_hook = """#!/bin/sh
# Pre-commit hook - kod kalitesi kontrolleri

echo "Pre-commit hook çalışıyor..."

# Python dosyalarını kontrol et
echo "Python kod stili kontrol ediliyor..."
if command -v flake8 >/dev/null 2>&1; then
    flake8 src/ tests/
    if [ $? -ne 0 ]; then
        echo "❌ Flake8 hatası buldu. Commit iptal edildi."
        exit 1
    fi
fi

# Büyük dosyaları kontrol et
echo "Büyük dosyalar kontrol ediliyor..."
git diff --cached --name-only | while read file; do
    if [ -f "$file" ]; then
        size=$(stat -f%z "$file" 2>/dev/null || stat -c%s "$file" 2>/dev/null)
        if [ $size -gt 10485760 ]; then  # 10MB
            echo "❌ Hata: $file dosyası çok büyük (>10MB)"
            exit 1
        fi
    fi
done

echo "✅ Pre-commit kontrolleri başarılı!"
exit 0
"""

    try:
        with open(f"{hooks_dir}/pre-commit", "w") as f:
            f.write(pre_commit_hook)
        os.chmod(f"{hooks_dir}/pre-commit", 0o755)
        print("Pre-commit hook oluşturuldu.")
    except:
        print("Hook oluşturulamadı (normal davranış).")

### 9.2. Git Alias'ları ve Produktivite İpuçları

In [ ]:
# Faydalı git alias'ları konfigüre edelim
useful_aliases = [
    ('st', 'status'),
    ('co', 'checkout'),
    ('br', 'branch'),
    ('ci', 'commit'),
    ('unstage', 'reset HEAD --'),
    ('last', 'log -1 HEAD'),
    ('visual', '!gitk'),
    ('tree', 'log --graph --oneline --all'),
    ('aliases', 'config --get-regexp alias'),
    ('cleanup', 'branch --merged | grep -v "\\*\\|main\\|develop" | xargs -n 1 git branch -d')
]

print("Faydalı Git alias'ları:")
for alias, command in useful_aliases:
    run_git_command(f'config alias.{alias} "{command}"', f'Alias ekleniyor: {alias}', False)
    print(f"git {alias} -> git {command}")

# Alias'ları test edelim
run_git_command("aliases", "Yapılandırılmış alias'lar")

### 9.3. Git Bisect: Bug Hunting

In [ ]:
# Git bisect için örnek senaryo oluşturalım
print("\n=== GIT BISECT DEMO ===")

# Birkaç commit oluşturalım, aralarında bug introducer olacak
def create_commits_with_bug():
    """Bug içeren commit serisi oluşturur."""

    # v1.0 - çalışan kod
    working_code = """
def calculate_average(numbers):
    \"\"\"Sayıların ortalamasını hesaplar.\"\"\"
    if not numbers:
        return 0
    return sum(numbers) / len(numbers)

def calculate_sum(numbers):
    \"\"\"Sayıların toplamını hesaplar.\"\"\"
    return sum(numbers)

if __name__ == "__main__":
    test_numbers = [1, 2, 3, 4, 5]
    print(f"Ortalama: {calculate_average(test_numbers)}")
    print(f"Toplam: {calculate_sum(test_numbers)}")
"""

    with open("src/calculator.py", "w") as f:
        f.write(working_code)
    run_git_command("add .", "", False)
    run_git_command('commit -m "v1.0: Hesaplama modülü eklendi"', "", False)

    # v1.1 - özellik ekleme
    enhanced_code = working_code.replace(
        'if __name__ == "__main__":',
        '''def calculate_median(numbers):
    """Sayıların medyanını hesaplar."""
    if not numbers:
        return 0
    sorted_numbers = sorted(numbers)
    n = len(sorted_numbers)
    if n % 2 == 0:
        return (sorted_numbers[n//2-1] + sorted_numbers[n//2]) / 2
    return sorted_numbers[n//2]

if __name__ == "__main__":'''
    )

    with open("src/calculator.py", "w") as f:
        f.write(enhanced_code)
    run_git_command("add .", "", False)
    run_git_command('commit -m "v1.1: Medyan hesaplama eklendi"', "", False)

    # v1.2 - BUG! (sıfıra bölme hatası)
    buggy_code = enhanced_code.replace(
        'return sum(numbers) / len(numbers)',
        'return sum(numbers) / (len(numbers) - 1)  # BUG: Off-by-one error!'
    )

    with open("src/calculator.py", "w") as f:
        f.write(buggy_code)
    run_git_command("add .", "", False)
    run_git_command('commit -m "v1.2: Performans optimizasyonu"', "", False)

    # v1.3 - başka özellik
    with open("src/calculator.py", "a") as f:
        f.write("\n\n# Versiyon 1.3 - Yeni yorum satırı\n")
    run_git_command("add .", "", False)
    run_git_command('commit -m "v1.3: Dokümantasyon güncellendi"', "", False)

create_commits_with_bug()

print("Bug içeren commit serisi oluşturuldu.")
run_git_command("log --oneline", "Son commit'ler")

### 9.4. Advanced Git Commands

In [ ]:
# Diğer önemli Git komutları
print("\n=== GELİŞMİŞ GIT KOMUTLARI ===")

# Git reflog - kayıp commit'leri bulma
run_git_command("reflog --oneline -10", "Son 10 Git işlemi (reflog)")

# Git cherry-pick için örnek
run_git_command("checkout -b hotfix-branch", "Hotfix dalı oluşturuluyor")

# Hotfix commit
with open("src/calculator.py", "r") as f:
    content = f.read()

content = content.replace("# BUG: Off-by-one error!", "# FIXED: Restored original logic")
content = content.replace("len(numbers) - 1", "len(numbers)")

with open("src/calculator.py", "w") as f:
    f.write(content)

run_git_command("add .", "", False)
run_git_command('commit -m "Hotfix: Ortalama hesaplama hatası düzeltildi"', "Hotfix commit'i")

# Ana dala dönüp cherry-pick yapma
run_git_command("checkout main", "Ana dala dönüş")
run_git_command("cherry-pick hotfix-branch", "Hotfix'i ana dala cherry-pick")

## 10. En İyi Uygulamalar ve Pratik İpuçları

### 10.1. Commit Message Kuralları

In [ ]:
print("\n=== COMMIT MESSAGE EN İYİ UYGULAMALARI ===")

commit_message_guide = """
# İYİ COMMIT MESAJI YAPISI:

# Başlık (50 karakter veya daha az)
# |<----  50 karakter sınırını göstermek için  ---->|

# Boş satır

# Gövde (72 karakter satır uzunluğu)
# |<----   72 karakter sınırını göstermek için    ---->|
# Neden bu değişikliğin gerekli olduğunu açıklayın.
# Neyi değil, NEDEN değiştirdiğinizi açıklayın.
#
# - Maddeler halinde yazabilirsiniz
# - Çok madde varsa pull request açın
#
# Footer'da issue referansları:
# Fixes: #123
# Closes: #456
# Related: #789

# ÖRNEKLER:

# ✅ İYİ ÖRNEKLER:
# "Müşteri churn modelinde özellik seçimi iyileştirildi"
# "API endpoint'inde authentication bug'ı düzeltildi"
# "Docker container'ı için memory limit ayarlandı"

# ❌ KÖTÜ ÖRNEKLER:
# "fix" (çok genel)
# "minor changes" (bilgi vermiyor)
# "asdasdas" (anlamsız)
# "WIP work in progress" (commit etmeyin)

# TİP PREFIKSLERI:
# feat: Yeni özellik
# fix: Bug düzeltmesi
# docs: Dokümantasyon
# style: Kod formatı (işlevsellik değişikliği yok)
# refactor: Refactoring (bug fix veya yeni özellik değil)
# test: Test ekleme/düzeltme
# chore: Build process veya auxiliary tool değişiklikleri
"""

print(commit_message_guide)

### 10.2. Git Workflow Best Practices

In [ ]:
workflow_guide = """
=== VERİ BİLİMİ PROJELERİ İÇİN GIT WORKFLOW ===

1. BRANCH STRATEJİSİ:
   ├── main (production-ready)
   ├── develop (integration branch)
   ├── feature/model-improvements
   ├── feature/data-preprocessing
   ├── experiment/new-algorithm
   └── hotfix/critical-bug

2. NAMING CONVENTIONS:
   • feature/açıklayıcı-isim
   • experiment/algoritma-adı
   • hotfix/kısa-açıklama
   • docs/güncelleme-konusu

3. COMMIT SIKLIĞI:
   • Küçük, atomik commit'ler yapın
   • Her commit çalışan kod olmalı
   • Günde birden fazla commit normal
   • WIP commit'leri yapmayın

4. PULL REQUEST SÜRECİ:
   • Her PR bir konuya odaklanmalı
   • Self-review yapın
   • Açıklayıcı başlık ve açıklama
   • Screenshot ekleyin (görsel değişiklik varsa)
   • CI/CD geçmesini bekleyin

5. CODE REVIEW:
   • Constructive feedback verin
   • Kodun logic'ini anlayın
   • Best practice'leri kontrol edin
   • Documentation yeterli mi?

6. VERİ VE MODEL YÖNETİMİ:
   • Büyük dosyaları Git'e eklemeyin
   • DVC veya Git LFS kullanın
   • Model versiyonlarını tag'leyin
   • Experiment metadata'sını kaydedin

7. GÜVENLİK:
   • API key'leri commit etmeyin
   • .env dosyalarını .gitignore'a ekleyin
   • Hassas verileri repository'de tutmayın
   • Pre-commit hook'ları kullanın
"""

print(workflow_guide)

### Alıştırma: Kapsamlı Git Senaryosu

Aşağıdaki senaryoyu gerçekleştirin:

1. **Yeni özellik dalı:** `feature/model-evaluation` oluşturun
2. **Model değerlendirme modülü** ekleyin (cross-validation, metrics)
3. **Conflict oluşturun:** Aynı dosyayı main'de de değiştirin
4. **Conflict çözün:** Manual veya tool kullanarak
5. **Stash kullanın:** Yarım kalmış değişiklikleri saklayın
6. **Cherry-pick:** Başka daldan bir commit alın
7. **Tag oluşturun:** Stable versiyonu işaretleyin
8. **Clean up:** Gereksiz dalları silin

In [ ]:
def comprehensive_git_exercise():
    """Kapsamlı Git alıştırması."""
    print("\n=== KAPSAMLI GIT ALIŞTIRMASİ ===")

    # 1. Yeni özellik dalı
    run_git_command("checkout -b feature/model-evaluation", "Model değerlendirme dalı")

    # 2. Model değerlendirme modülü
    evaluation_module = """
import numpy as np
from sklearn.model_selection import cross_val_score, StratifiedKFold
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
from sklearn.metrics import confusion_matrix, classification_report
import matplotlib.pyplot as plt
import seaborn as sns

class ModelEvaluator:
    \"\"\"Model değerlendirme sınıfı.\"\"\"

    def __init__(self, model):
        self.model = model
        self.cv_scores = None
        self.test_metrics = None

    def cross_validate(self, X, y, cv_folds=5):
        \"\"\"Cross-validation ile model değerlendirme.\"\"\"
        skf = StratifiedKFold(n_splits=cv_folds, shuffle=True, random_state=42)

        # Farklı metrikler için cross-validation
        metrics = ['accuracy', 'precision', 'recall', 'f1']
        cv_results = {}

        for metric in metrics:
            scores = cross_val_score(self.model, X, y, cv=skf, scoring=metric)
            cv_results[metric] = {
                'scores': scores,
                'mean': scores.mean(),
                'std': scores.std()
            }

        self.cv_scores = cv_results
        return cv_results

    def evaluate_test_set(self, X_test, y_test):
        \"\"\"Test seti üzerinde detaylı değerlendirme.\"\"\"
        y_pred = self.model.predict(X_test)

        metrics = {
            'accuracy': accuracy_score(y_test, y_pred),
            'precision': precision_score(y_test, y_pred, average='weighted'),
            'recall': recall_score(y_test, y_pred, average='weighted'),
            'f1': f1_score(y_test, y_pred, average='weighted')
        }

        self.test_metrics = metrics
        return metrics

    def plot_confusion_matrix(self, X_test, y_test, save_path=None):
        \"\"\"Confusion matrix çizer.\"\"\"
        y_pred = self.model.predict(X_test)
        cm = confusion_matrix(y_test, y_pred)

        plt.figure(figsize=(8, 6))
        sns.heatmap(cm, annot=True, fmt='d', cmap='Blues')
        plt.title('Confusion Matrix')
        plt.xlabel('Predicted')
        plt.ylabel('Actual')

        if save_path:
            plt.savefig(save_path, dpi=300, bbox_inches='tight')

        plt.show()

    def generate_report(self):
        \"\"\"Kapsamlı değerlendirme raporu oluşturur.\"\"\"
        report = "=== MODEL DEĞERLENDİRME RAPORU ===\\n\\n"

        if self.cv_scores:
            report += "Cross-Validation Sonuçları:\\n"
            for metric, results in self.cv_scores.items():
                report += f"{metric.capitalize()}: {results['mean']:.4f} (+/- {results['std']*2:.4f})\\n"

        if self.test_metrics:
            report += "\\nTest Seti Sonuçları:\\n"
            for metric, value in self.test_metrics.items():
                report += f"{metric.capitalize()}: {value:.4f}\\n"

        return report

if __name__ == "__main__":
    print("Model değerlendirme modülü hazır.")
"""

    with open("src/models/evaluate_model.py", "w", encoding="utf-8") as f:
        f.write(evaluation_module)

    run_git_command("add .", "", False)
    run_git_command('commit -m "Model değerlendirme modülü eklendi\\n\\n- Cross-validation desteği\\n- Test seti değerlendirmesi\\n- Confusion matrix görselleştirmesi\\n- Kapsamlı rapor oluşturma"',
                    "Model evaluation commit")

    # 3-4. Conflict oluşturma ve çözme
    run_git_command("checkout main", "Ana dala geçiş")

    # Ana dalda aynı dosyayı farklı şekilde değiştir
    simple_eval = """
def simple_accuracy(y_true, y_pred):
    \"\"\"Basit accuracy hesaplama.\"\"\"
    correct = sum(1 for true, pred in zip(y_true, y_pred) if true == pred)
    return correct / len(y_true)

print("Basit değerlendirme modülü")
"""

    with open("src/models/evaluate_model.py", "w") as f:
        f.write(simple_eval)

    run_git_command("add .", "", False)
    run_git_command('commit -m "Basit model değerlendirme eklendi"', "", False)

    # Conflict oluştur ve çöz
    print("Conflict oluşturuluyor ve çözülüyor...")
    run_git_command("merge feature/model-evaluation", "Conflict oluşturma", False)
    run_git_command("checkout --theirs src/models/evaluate_model.py", "Gelişmiş versiyon seçiliyor", False)
    run_git_command("add .", "", False)
    run_git_command('commit -m "Merge conflict çözüldü: Gelişmiş model evaluation korundu"', "", False)

    # 7. Tag oluşturma
    run_git_command("tag -a v1.0.0 -m 'Stable release: Basic ML pipeline completed'", "Stable versiyon tag'i")
    run_git_command("tag", "Mevcut tag'lar")

    print("✅ Kapsamlı Git alıştırması tamamlandı!")

# Alıştırmayı çalıştır
comprehensive_git_exercise()

## Haftanın Özeti

Bu hafta kapsamlı bir Git eğitimi tamamladık:

### Öğrendiklerimiz:
1. **Temel Git işlemleri:** init, add, commit, status, log, diff
2. **Branching ve merging:** Feature-branch workflow, conflict çözme
3. **Git Stash:** Geçici değişiklikleri yönetme
4. **PyCharm entegrasyonu:** IDE üzerinden Git operasyonları
5. **GitHub workflow:** Pull requests, code review, CI/CD
6. **İleri düzey teknikler:** Hooks, bisect, cherry-pick, reflog
7. **Best practices:** Commit mesajları, workflow stratejileri

### Pratik Beceriler:
- ✅ Git repository'si yönetimi
- ✅ Conflict çözme yöntemleri
- ✅ Stash kullanımı
- ✅ PyCharm Git tools kullanımı
- ✅ GitHub collaboration
- ✅ Professional workflow patterns

### Sonraki Adımlar

Artık projelerinizi profesyonel seviyede versiyon kontrol altında tutabiliyorsunuz. **Hafta 2: Kod ve Veri için Test Stratejileri**'nde, yazdığımız kodun doğruluğunu garanti altına almak için test yazma disiplinini öğreneceğiz. Git ile test süreçlerini nasıl entegre edeceğimizi ve sürekli entegrasyon (CI) temellerini atacağız.

### Git Komutları Özet Tablosu

| Kategori | Komut | Açıklama |
|----------|-------|----------|
| **Başlangıç** | `git init` | Repository başlatır |
| | `git clone <url>` | Remote repository'yi klonlar |
| **Temel İşlemler** | `git status` | Çalışma dizini durumu |
| | `git add <file>` | Dosyayı staging area'ya ekler |
| | `git commit -m "mesaj"` | Değişiklikleri commit eder |
| | `git log` | Commit geçmişini gösterir |
| **Branching** | `git branch` | Dalları listeler |
| | `git checkout -b <branch>` | Yeni dal oluşturur ve geçer |
| | `git merge <branch>` | Dalı birleştirir |
| | `git branch -d <branch>` | Dalı siler |
| **Stash** | `git stash` | Değişiklikleri saklar |
| | `git stash pop` | Son stash'i geri getirir |
| | `git stash list` | Stash listesini gösterir |
| **Remote** | `git remote add origin <url>` | Remote ekler |
| | `git push` | Değişiklikleri remote'a gönderir |
| | `git pull` | Remote'dan değişiklikleri çeker |
| **İleri Düzey** | `git cherry-pick <commit>` | Belirli commit'i alır |
| | `git reflog` | Tüm Git işlemlerini gösterir |
| | `git bisect` | Binary search ile bug bulur |
| | `git tag <name>` | Tag oluşturur |

Temizlik
os.chdir(original_dir)
print(f"\n=== DERS TAMAMLANDI ===")
print(f"Çalışma dizini: {os.getcwd()}")
print("✅ Hafta 1: Git ve GitHub dersi başarıyla tamamlandı!")